In [2]:
import ase
import numpy as np
import os
import json
import ubjson
from ase.io import read
from ase.visualize import view
from ase.neighborlist import neighbor_list
from tqdm.notebook import tqdm

In [33]:
import signac
import os
import sys
sys.path.insert(0,'./scripts/')
from utils.io import tojson, fromjson

In [34]:
data = fromjson('./scripts/spherical_expansion/workspace/32a34936af7e7bfd02fdf77db8653a06/out_se_cpp.json')
data = data['results']
data['mem_max'] = 100
data['mem_unit'] = 'MiB'
tojson('./scripts/spherical_expansion/workspace/32a34936af7e7bfd02fdf77db8653a06/res_se_cpp.json', data)

In [31]:
project = signac.get_project('./scripts/spherical_expansion/')
for job in tqdm(project.find_jobs()):
   if len(os.listdir(job.fn(''))) < 4:
       print(job.id)

32a34936af7e7bfd02fdf77db8653a06



In [26]:
os.listdir(job.fn(''))

['signac_job_document.json',
 'res_si_cpp.json',
 'out_si_cpp.json',
 'in_si_cpp.json',
 'signac_statepoint.json']

In [21]:
project = signac.get_project('./scripts/spherical_invariants/')
for job in tqdm(project):
    path = job.fn('')
    if job.sp.name == 'silicon_bulk' and len(os.listdir(path)) > 1 and len(job.document) < 1:
        print(job.sp.name,os.listdir(path), job)

t.json'] 36fa3971fd320257486673379f6df470
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] 10ad8ed23aab42dead60c6602cf00e6d
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] e25289784e35c76b7439e556b8c51f8b
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] 920e8ecaab6a8d9be55f611de95a5442
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] 8cac1c826834bbccf619f9cd85c2fd1d
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] 07b1b3713daa415aa7064d14bdf9ba62
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] a812eafb2b67cefad931dd0beb0af81e
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in_si_cpp.json', 'signac_statepoint.json'] c5877b1e5415c3bf3014984e17f1c3fa
silicon_bulk ['res_si_cpp.json', 'out_si_cpp.json', 'in

In [14]:
project = signac.get_project('./scripts/spherical_invariants/')
len(project)

4480

In [17]:
project = signac.get_project('./scripts/spherical_invariants/')
ll = []
for job in tqdm(project):
    path = job.fn('')
    if len(job.document) < 1:
        #print(job.sp.name,os.listdir(path), job)
        ll.append(job.sp.name)
set(ll)

{'molecular_crystals', 'qm9', 'silicon_bulk'}

In [19]:
project = signac.get_project('./scripts/spherical_invariants/')
for job in tqdm(project):
    if len(job.document) < 1:
        #job.remove()
        path = job.fn('')
        p1 = path+'/in_si_cpp.json'
        p2 = path+'/out_si_cpp.json'
        p3 = path+'/res_si_cpp.json'
        if len(os.listdir(path)) > 1:
            try:
                os.remove(p1)
            except:
                pass
            try:
                os.remove(p2)
            except:
                pass
            try:
                os.remove(p3)
            except:
                pass

In [28]:
def fromfile(fn):
    _, extension = os.path.splitext(fn)
    if extension == '.json':
        with open(fn, 'rb') as f:
            data = json.load(f)
    elif extension == '.ubjson':
        with open(fn, 'rb') as f:
            data = ubjson.load(f)
    frames = []
    for idx in data['ids']:
        ff = data['{}'.format(idx)]
        frame = ase.Atoms(positions=ff['positions'], cell=ff['cell'], 
                          numbers=ff['numbers'], pbc=ff['pbc'])
        if 'info' in ff:
            frame.info = ff['info']
        if 'arrays' in ff:
            for k,v in ff['arrays'].items():
                frame.set_array(k, np.array(v))
        frames.append(frame)
    return frames

In [29]:
path = './structures/'
fns = ['qm9.json', 'molecular_crystals.json', 'silicon_bulk.json', 
       'methane_liquid.json', 'methane_sulfonic.ubjson']
frames = {}
for fn in fns:
    frames[fn] = fromfile(path+fn)

In [19]:
view(frames['qm9.json'])

In [20]:
view(frames['molecular_crystals.json'])

In [21]:
view(frames['silicon_bulk.json'])

In [36]:
sp = {
    'qm9.json' : {'st':0,'nd':500, 'c':4}, 
    'molecular_crystals.json' : {'st':400,'nd':450, 'c':4}, 
    'silicon_bulk.json' : {'st':600,'nd':700, 'c':4}, 
    'methane_liquid.json' : {'st':100,'nd':150, 'c':4}, 
    'methane_sulfonic.ubjson' : {'st':0,'nd':150, 'c':4}
}


for fn in sp:
    s = sp[fn]
    ffs = frames[fn][s['st']:s['nd']]
    nat = 0
    nneigh = 0
    for ii,ff in enumerate(ffs):
        if np.product(ff.get_pbc()):
            cl = ff.get_cell_lengths_and_angles()[:3]
            if np.any(cl < 2 * 4):
                print(fn, ii)
        i,j = ase.neighborlist.neighbor_list('ij', ff, s['c']) 
        nat += len(np.unique(i))
        nneigh += len(j)
    print(fn, nat, nneigh)
    # view(ffs)

qm9.json 8977 112120
molecular_crystals.json 0
molecular_crystals.json 2
molecular_crystals.json 3
molecular_crystals.json 4
molecular_crystals.json 6
molecular_crystals.json 7
molecular_crystals.json 8
molecular_crystals.json 9
molecular_crystals.json 10
molecular_crystals.json 12
molecular_crystals.json 14
molecular_crystals.json 17
molecular_crystals.json 18
molecular_crystals.json 19
molecular_crystals.json 20
molecular_crystals.json 22
molecular_crystals.json 26
molecular_crystals.json 27
molecular_crystals.json 28
molecular_crystals.json 29
molecular_crystals.json 30
molecular_crystals.json 31
molecular_crystals.json 34
molecular_crystals.json 35
molecular_crystals.json 41
molecular_crystals.json 43
molecular_crystals.json 46
molecular_crystals.json 47
molecular_crystals.json 48
molecular_crystals.json 6830 183684
silicon_bulk.json 8508 133980
methane_liquid.json 6750 104946
methane_sulfonic.ubjson 42125 115446


In [ ]:
ff.get_cell_lengths_and_angles

In [25]:
np.product?

In [ ]:
{'a': [...], 'b': [...], 'n1': [...], 'n2': [...], 'l': [...]}

In [1]:
import sys
sys.path.insert(0, './build/_deps/rascal-build/')
from rascal.representations import SphericalInvariants

In [8]:
SphericalInvariants?

In [18]:
frames = fromfile('./structures/qm9.json')[:500]
soap_params = []
soap = SphericalInvariants(interaction_cutoff=4,cutoff_smooth_width=0.5,max_radial=10,
                           max_angular=6,gaussian_sigma_type="Constant")
aa = soap.get_feature_index_mapping(frames)

In [20]:
len(aa)

10500

In [24]:
aa = b's'
if aa:
    print('sdf')

sdf


In [21]:
np.random.seed(10)
ids = np.arange(len(aa))
np.random.shuffle(ids)
sel = {'a': [],'b': [], 'n1': [], 'n2': [], 'l': []}
for idx in ids[:20]:
    a = aa[idx]
    for k,v in a.items():
        sel[k].append(v)
sel

{'a': [1, 6, 1, 1, 7, 1, 6, 6, 9, 8, 6, 1, 1, 1, 6, 7, 8, 6, 1, 8],
 'b': [8, 6, 9, 7, 7, 7, 6, 8, 9, 9, 8, 7, 7, 7, 8, 9, 8, 8, 9, 9],
 'n1': [8, 0, 6, 3, 7, 5, 7, 8, 0, 4, 1, 8, 9, 1, 9, 0, 1, 6, 2, 3],
 'n2': [1, 4, 7, 1, 4, 5, 3, 7, 4, 3, 3, 3, 9, 4, 7, 7, 7, 0, 5, 5],
 'l': [6, 2, 6, 2, 3, 5, 1, 6, 4, 0, 0, 4, 1, 3, 2, 0, 4, 4, 2, 0]}

In [22]:
read('./structures/qm9.json',':500')

[Atoms(symbols='NCNCNONO2H2', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C2NC4H7', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='NC6NCH8', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='CNC2OCNC2H8', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='OC3OC2OH8', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='CNC2NC2NCH11', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C4N3C2H9', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='ONC7H11', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C8NH11', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C7OCH12', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C2N2C2NH3COH6', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='NC2OCO2NCH4', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='NCOC4ONH8', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='OC3OCOCH6', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C3NC2OC2H13', pbc=False, cell=[10.0, 10.0, 10.0]),
 Atoms(symbols='C4NC3H

In [37]:
sys.path.insert(0, './scripts/')
from representation_params import REPRESENTATION_PARAMS

In [39]:
for aa in REPRESENTATION_PARAMS:
    if aa['name'] != 'qm9':
        print(aa['name'])

molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_cr

molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_cr

molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_cr

molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_cr

molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_crystals
molecular_cr

...

methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfon

methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfon

methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfon

methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfon

methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfonic
methane_sulfon